# Check CSV file
This notebook was used to analyse a CSV file with annotation information (*Kadaverbilder_leer.csv*) and find the referenced images.

In [1]:
%load_ext autoreload
%autoreload 2

import csv
from py.Dataset import Dataset
from py.Session import Session, MotionImage, LapseImage
from datetime import datetime

DIR = '/home/AMMOD_data/camera_traps/BayerWald/Vielkadaver-Projekt/'

ds = Dataset(DIR)

Found 32 sessions


In [2]:
def parse_datetime(datetime_str: str) -> datetime:
    return datetime.strptime(datetime_str[:-5], "%Y-%m-%dT%H:%M:%S")

assert parse_datetime("2021-05-28T09:55:24+0100") == datetime(2021, 5, 28, 9, 55, 24)

In [3]:
with open("Kadaverbilder_leer.csv", newline="") as csvfile:
    reader = csv.reader(csvfile, delimiter=";")
    header = next(reader)
    print("Header: ", header)
    session_col = header.index("deploymentID")
    datetime_col = header.index("timestamp")
    session_name: str = None
    session: Session = None
    successful = 0
    skipped = 0
    less_found = 0
    ambiguous = 0
    results = []
    last_date = None
    last_date_occurences = 0
    for row in reader:
        # print(row)
        # open session if not already opened
        if session_name != row[session_col]:
            session_name = row[session_col]
            print(f"Trying to create session {session_name}...")
            try:
                session = ds.create_session(session_name)
            except ValueError as e:
                print(e)
                session = None
        if session is None:
            skipped += 1
        else:
            # get datetime
            date = parse_datetime(row[datetime_col])
            if date == last_date:
                last_date_occurences += 1
            else:
                # look for images
                images = session.get_motion_images_from_date(last_date)

                if len(images) < last_date_occurences:
                    less_found += last_date_occurences
                elif len(images) > last_date_occurences:
                    ambiguous += last_date_occurences
                else:
                    for image in images:
                        results.append([session.name, image.filename])
                    successful += last_date_occurences

                last_date = date
                last_date_occurences = 1
print(f"Successfully found {successful} images")
print(f"Skipped {skipped} images because session was not found")
print(f"For {less_found} session dates less images were found than specified (inconsistency)")
print(f"For {ambiguous} session dates more images were found than specified (ambiguous)")


Header:  ['observationID', 'deploymentID', 'sequenceID', 'mediaID', 'timestamp', 'observationType', 'cameraSetup', 'taxonID', 'scientificName', 'count', 'countNew', 'lifeStage', 'sex', 'behaviour', 'individualID', 'classificationMethod', 'classifiedBy', 'classificationTimestamp', 'classificationConfidence', 'comments', '_id']
Trying to create session VIELAAS_Spring_Session03-VIELAAS_Beaver_03...
There are no sessions matching this name: []
Trying to create session VIELAAS_Spring_Session03-VIELAAS_Ermine_03...
There are no sessions matching this name: []
Trying to create session VIELAAS_Spring_Session03-VIELAAS_Fox_03...
Session 'Fox_03' at folder: /home/AMMOD_data/camera_traps/BayerWald/Vielkadaver-Projekt/VIELAAS_Spring_Session03-VIELAAS_Fox_03
Loaded scans.
Generating motion map...
Trying to create session VIELAAS_Spring_Session03-VIELAAS_Rat_03...
There are no sessions matching this name: []
Successfully found 3695 images
Skipped 138 images because session was not found
For 0 sessio

In [4]:
import numpy as np
np.save("csv_test_images.npy", results)

In [5]:
l = []
for i in range(3600):
    if ["Fox_03", f"Fox_03_{i:05d}.jpg"] not in results:
        l.append(i)
print(l)

[0, 1, 2, 3, 4, 5, 431, 432, 433, 434, 435, 436, 437, 438, 439, 440, 441, 442, 443, 444, 445, 446, 447, 448, 449, 450, 451, 452, 453, 454, 455, 456, 457, 458, 459, 460, 461, 462, 463, 464, 465, 466, 467, 468, 469, 470, 471, 472, 473, 474, 475, 476, 477, 478, 479, 480, 2176, 2177, 2178, 2179, 2180, 2181, 2182, 2183, 2184, 2185, 2186, 2187, 2188, 2189, 2190, 2286, 2287, 2288, 2289, 2290, 2291, 2292, 2293, 2294, 2295, 2326, 2327, 2328, 2329, 2330, 2331, 2332, 2333, 2334, 2335, 2336, 2337, 2338, 2339, 2340, 2341, 2342, 2343, 2344, 2345, 2346, 2347, 2348, 2349, 2350, 2351, 2352, 2353, 2354, 2355, 2356, 2357, 2358, 2359, 2360, 2361, 2362, 2363, 2364, 2365, 2366, 2367, 2368, 2369, 2370, 2371, 2372, 2373, 2374, 2375, 2376, 2377, 2378, 2379, 2380, 2381, 2382, 2383, 2384, 2385, 2386, 2387, 2388, 2389, 2390, 2391, 2392, 2393, 2394, 2395, 2396, 2397, 2398, 2399, 2400, 2401, 2402, 2403, 2404, 2405, 2406, 2407, 2408, 2409, 2410, 2411, 2412, 2413, 2414, 2415, 2416, 2417, 2418, 2419, 2420, 2421, 2422,